# FBMC Chronos-2 Zero-Shot Inference - Full Production Forecast

**Production run**: 38 borders × 14 days (336 hours)

This notebook runs complete zero-shot forecasts for all FBMC borders on HuggingFace Space with GPU.

## 1. Environment Setup

In [ ]:
import time
import os
import polars as pl
import torch
from datetime import datetime, timedelta
from datasets import load_dataset
from chronos import ChronosPipeline
import altair as alt
from pathlib import Path

# Add src to path for imports
import sys
sys.path.append('/home/user/app/src')  # HF Space path

from forecasting.dynamic_forecast import DynamicForecast
from forecasting.feature_availability import FeatureAvailability

print("Environment setup complete")
print(f"PyTorch version: {torch.__version__}")
print(f"GPU available: {torch.cuda.is_available()}")
if torch.cuda.is_available():
    print(f"GPU device: {torch.cuda.get_device_name(0)}")

## 2. Load Extended Dataset from HuggingFace

In [ ]:
print("Loading dataset from HuggingFace...")
start_time = time.time()

# Load dataset
hf_token = os.getenv("HF_TOKEN")
dataset = load_dataset(
    "evgueni-p/fbmc-features-24month",
    split="train",
    token=hf_token
)

# Convert to Polars
df = pl.from_arrow(dataset.data.table)

print(f"✓ Loaded: {df.shape}")
print(f"  Date range: {df['timestamp'].min()} to {df['timestamp'].max()}")
print(f"  Load time: {time.time() - start_time:.1f}s")

## 3. Configure Dynamic Forecast System

In [ ]:
# Categorize features by availability
categories = FeatureAvailability.categorize_features(df.columns)

print("Feature categorization:")
print(f"  Full-horizon D+14: {len(categories['full_horizon_d14'])} features")
print(f"  Partial D+1: {len(categories['partial_d1'])} features")
print(f"  Historical only: {len(categories['historical'])} features")
print(f"  Total: {sum(len(v) for v in categories.values())} features")

# Identify target borders
target_cols = [col for col in df.columns if col.startswith('target_border_')]
borders = [col.replace('target_border_', '') for col in target_cols]
print(f"\n✓ Found {len(borders)} borders")
print(f"  Borders: {', '.join(borders[:5])}...")

## 4. Load Chronos-2 Model on GPU

In [ ]:
print("Loading Chronos-2 Large model...")
start_time = time.time()

pipeline = ChronosPipeline.from_pretrained(
    "amazon/chronos-t5-large",
    device_map="cuda",
    torch_dtype=torch.bfloat16
)

print(f"✓ Model loaded in {time.time() - start_time:.1f}s")
print(f"  Device: {next(pipeline.model.parameters()).device}")
print(f"  Dtype: {next(pipeline.model.parameters()).dtype}")

## 5. Run Zero-Shot Inference for All Borders

In [ ]:
# Production configuration
prediction_hours = 336  # 14 days
context_hours = 512     # Context window
run_date = datetime(2025, 9, 30, 23, 0)  # Sept 30 11 PM

print("Production forecast configuration:")
print(f"  Run date: {run_date}")
print(f"  Context: {context_hours} hours")
print(f"  Forecast: {prediction_hours} hours (14 days)")
print(f"  Forecast range: Oct 1 00:00 to Oct 14 23:00")
print(f"  Borders: {len(borders)}")
print()

# Initialize dynamic forecast
forecaster = DynamicForecast(
    df=df,
    feature_categories=categories
)

# Storage for all forecasts
all_forecasts = {}
inference_times = {}

# Run inference for each border
total_start = time.time()

for i, border in enumerate(borders, 1):
    print(f"[{i}/{len(borders)}] Processing {border}...", end=" ")
    
    try:
        # Extract data
        context_data, future_data = forecaster.prepare_forecast_data(
            run_date=run_date,
            border=border
        )
        
        # Get context (last 512 hours)
        context = context_data.select([border]).to_numpy()[-context_hours:].flatten()
        
        # Run inference
        start_time = time.time()
        forecast = pipeline.predict(
            context=context,
            prediction_length=prediction_hours,
            num_samples=20
        )
        elapsed = time.time() - start_time
        
        # Store median forecast
        forecast_median = forecast.numpy().median(axis=0)
        all_forecasts[border] = forecast_median
        inference_times[border] = elapsed
        
        print(f"✓ {elapsed:.1f}s")
        
    except Exception as e:
        print(f"✗ ERROR: {str(e)}")
        all_forecasts[border] = None
        inference_times[border] = 0.0

total_time = time.time() - total_start

print("\n" + "="*60)
print("INFERENCE COMPLETE")
print("="*60)
print(f"Total time: {total_time/60:.1f} minutes")
print(f"Avg per border: {total_time/len(borders):.1f}s")
print(f"Successful: {sum(1 for v in all_forecasts.values() if v is not None)}/{len(borders)}")

## 6. Save Forecasts to Parquet

In [ ]:
# Create timestamp range for forecasts
forecast_timestamps = pl.datetime_range(
    datetime(2025, 10, 1, 0, 0),
    datetime(2025, 10, 14, 23, 0),
    interval='1h',
    eager=True
)

# Build forecast DataFrame
forecast_data = {'timestamp': forecast_timestamps}
for border, forecast in all_forecasts.items():
    if forecast is not None:
        forecast_data[f'forecast_{border}'] = forecast.tolist()
    else:
        forecast_data[f'forecast_{border}'] = [None] * len(forecast_timestamps)

forecast_df = pl.DataFrame(forecast_data)

# Save to parquet
output_path = Path('/home/user/app/forecasts_14day.parquet')
forecast_df.write_parquet(output_path)

print(f"✓ Forecasts saved: {forecast_df.shape}")
print(f"  File: {output_path}")
print(f"  Size: {output_path.stat().st_size / 1024 / 1024:.1f} MB")

## 7. Visualize Sample Borders

In [ ]:
# Select 4 representative borders for visualization
sample_borders = borders[:4]

charts = []
for border in sample_borders:
    if all_forecasts[border] is not None:
        viz_data = pl.DataFrame({
            'timestamp': forecast_timestamps,
            'forecast': all_forecasts[border].tolist()
        })
        
        chart = alt.Chart(viz_data.to_pandas()).mark_line().encode(
            x=alt.X('timestamp:T', title='Date'),
            y=alt.Y('forecast:Q', title='Flow (MW)'),
            tooltip=['timestamp:T', alt.Tooltip('forecast:Q', format='.0f')]
        ).properties(
            width=400,
            height=200,
            title=f'{border}'
        )
        charts.append(chart)

# Combine into 2x2 grid
combined = alt.vconcat(
    alt.hconcat(charts[0], charts[1]),
    alt.hconcat(charts[2], charts[3])
).properties(
    title='Sample Zero-Shot Forecasts (Oct 1-14, 2025)'
)

combined

## 8. Performance Summary

In [ ]:
# Create performance summary
perf_data = pl.DataFrame({
    'border': list(inference_times.keys()),
    'inference_time_s': list(inference_times.values()),
    'status': ['SUCCESS' if all_forecasts[b] is not None else 'FAILED' for b in inference_times.keys()]
}).sort('inference_time_s', descending=True)

print("\nTop 10 Slowest Borders:")
print(perf_data.head(10))

print("\nPerformance Statistics:")
print(f"  Mean: {perf_data['inference_time_s'].mean():.1f}s")
print(f"  Median: {perf_data['inference_time_s'].median():.1f}s")
print(f"  Min: {perf_data['inference_time_s'].min():.1f}s")
print(f"  Max: {perf_data['inference_time_s'].max():.1f}s")

print("\n" + "="*60)
print("PRODUCTION FORECAST COMPLETE")
print("="*60)
print(f"Borders processed: {len(borders)}")
print(f"Forecast horizon: 14 days (336 hours)")
print(f"Total runtime: {total_time/60:.1f} minutes")
print(f"Output: forecasts_14day.parquet")
print(f"\n✓ Ready for evaluation against Oct 1-14 actuals")